In [1]:
!pip install pytdc
!pip install torch

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [3]:
import os
import csv
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
from tdc.resource.pinnacle import PINNACLE
from tdc.benchmark_group import scdti_group

pinnacle = PINNACLE()
embeds = pinnacle.get_embeds()
print(embeds)

/home/jesusca/.local/lib/python3.11/site-packages/pandas/core/arrays/masked.py:60: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (
Downloading...
100%|██████████| 2.57M/2.57M [00:00<00:00, 7.62MiB/s]
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 4.38MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:13<00:00, 14.5MiB/s] 
Downloading...
100%|██████████| 20.5M/20.5M [00:01<00:00, 13.9MiB/s]


                                               0         1         2    \
FSTL1--epithelial cell of lacrimal sac   -0.014363 -0.004553 -0.016610   
YAP1--epithelial cell of lacrimal sac    -0.011285 -0.001775 -0.010964   
POLR1D--epithelial cell of lacrimal sac  -0.015468 -0.002891 -0.015947   
CCDC183--epithelial cell of lacrimal sac -0.016569 -0.001287 -0.012962   
ARHGEF5--epithelial cell of lacrimal sac -0.026593 -0.005891 -0.020471   
...                                            ...       ...       ...   
PYCARD--cd24 neutrophil                  -0.004634 -0.004895 -0.021035   
VAV1--cd24 neutrophil                    -0.005778 -0.005027 -0.022879   
RHOA--cd24 neutrophil                    -0.003144 -0.004970 -0.013667   
RBBP5--cd24 neutrophil                   -0.004313 -0.004756 -0.022853   
SUMO1P1--cd24 neutrophil                 -0.001336 -0.007367 -0.026235   

                                               3         4         5    \
FSTL1--epithelial cell of lacrimal sa

In [12]:
# the output is binary classification. Our MLP comprises an input feedforward neural network, one hidden feedforward neural network layer and
# an output feedforward neural network layer. In between each layer, we have a nonlinear activation layer. In addition, we use dropout and normalization
# layers between the input and hidden layer (see ‘Implementation’ section for more information). Our objective function is binary cross-entropy loss.

class MLP(nn.Module):
    def __init__(self, input_size, hidden_sizes, dropout_rate, norm, actn, order, output_size):
        super(MLP, self).__init__()

        self.n_layer = len(hidden_sizes) - 1
        self.input_size = input_size
        actn = nn.ReLU()

        # input layer
        layers = [nn.Linear(self.input_size, hidden_sizes[0]), actn]

        # hidden layers
        for i in range(self.n_layer):
            layers += self.compose_layer(hidden_sizes[i], hidden_sizes[i+1], norm, actn, dropout_rate, order)

        # output layers
        layers.append(nn.Linear(hidden_sizes[-1], 1))
        
        print(layers)

        self.fc = nn.Sequential(*layers)

    def compose_layer(self, input_size, output_size, norm, actn, dropout_rate, order):
        if norm == 'bn':
            norm = nn.BatchNorm1d(input_size)
        elif norm == 'ln':
            norm = nn.LayerNorm(input_size)
        else:
            norm = None

        # add norm and dropout layers based on which should happen first (hyperparameter)
        if order == 'nd':
            layers = [norm] if norm else []
            if (abs(dropout_rate - 0)) >= 1e-8:
                layers.append(nn.Dropout(dropout_rate))
        elif order == 'dn':
            layers = [nn.Dropout(dropout_rate)] if (abs(dropout_rate - 0)) >= 1e-8 else []
            if norm:
                layers.append(norm)
        else:
            raise NotImplemented

        layers.append(nn.Linear(input_size, output_size))
        layers.append(actn)

        return layers

    def forward(self, x):
        output = self.fc(x)
        return output
        

# pandas row to Torch tensor
def row_to_tensor(row):
    return torch.tensor(row.values.tolist())

# adds Single Cell Drug Target Identification information from TDC to training data
def generate_data_target(train):
    for _, row in train.iterrows():
        try: 
            prot = row["name"]
            ct = row["cell_type_label"]
            idx = "{}--{}".format(prot, ct)
            embed = embeds.loc[[idx]]
            target = row["y"]
            yield row_to_tensor(embed), torch.FloatTensor([[target]])
        except KeyError: 
            print(f"{idx} was not found, continuing")
            target = row["y"]
            yield [], torch.FloatTensor([[target]])


# Optimal Hyperparameters as defined by the Pinnacle paper for Rheumatoid Arthritis (EFO_0000685)
hyperp_ra = {'actn': 'relu', 'd': .2, 'hidden_sizes': [32, 8], 'lr': 0.01, 'norm': 'ln',
             'order': 'dn', 'wd': .001, 'random_state': 1, 'num_epoch': 1}


# Optimal Hyperparameters as defined by the Pinnacle paper for Inflammatory bowel disease (EFO_0003767)
hyperp_ibd = {'actn': 'relu', 'd': .4, 'hidden_sizes': [32,8], 'lr': 0.001, 'norm': 'ln',
             'order': 'nd', 'wd': .0001, 'random_state': 1, 'num_epoch': 1}


In [16]:
seed_results = []


for i in range(1, 11):
    group = scdti_group.SCDTIGroup()
    train_val = group.get_train_valid_split(seed=i)
    assert "train" in train_val, "no training set"
    assert "val" in train_val, "no validation set"
    assert len(train_val["train"]) > 0, "no entries in training set"
    tst = group.get_test(i)["test"]

    train = train_val["train"]

    input_size = embeds.shape[1]
    output_size = 1
    disease = tst["disease"][0]
    
    print(tst.head())

    # Make model using hyperp based on disease
    if disease == "RA":
        hyperp = hyperp_ra
    else:
        hyperp = hyperp_ibd


    model = MLP(input_size, hyperp['hidden_sizes'], hyperp['d'], hyperp['norm'], hyperp['actn'], hyperp['order'],
                output_size)

    # set up criterion, make sure it's the correct one
    # Example usage with a loss function
    criterion = nn.BCEWithLogitsLoss()

    # train using the train data
    # You'll need to prepare your training data (input and target) in the correct format
    # Then, you can use the model for training:
    optimizer = torch.optim.Adam(model.parameters())
    for epoch in range(hyperp['num_epoch']):
        for input_data, target_data in generate_data_target(train):
            if len(input_data) == 0:
                continue
            optimizer.zero_grad()
            output = model(input_data)
            loss = criterion(output, target_data)
            loss.backward()
            optimizer.step()
    print("done training")


    # get predictions on the testing data and evaluate
    # prompt: perform prediction on the results of running generate_data_target function over the tst valirable data

    predictions = []
    for input_data, _ in generate_data_target(tst):
        if len(input_data) == 0:
            predictions.append(0)
            continue
        with torch.no_grad():
            output = model(input_data)
            predictions.append(output.item())
    print(len(predictions))
    print(len(tst["disease"]))
    tst["preds"] = predictions
    results = group.evaluate(tst, seed=i)
    seed_results.append(results)
    print(results)

    print('past results')
    
    # save weights, biases, model predictions, and results
    weights_file = f"Model_Weights_Biases{i}"
    pred_file = f"Model_Preds{i}"
    folder_path = os.getcwd()
    weights_file_path = os.path.join(folder_path, weights_file)
    pred_file_path = os.path.join(folder_path, pred_file)
    
    state_dict = model.state_dict()

    with open(weights_file_path, 'w', newline='') as csvfile:
        writer = csv.writer(csvfile)

        writer.writerow(['layer_name', 'weight/bias', 'value'])
        for layer_name, param in state_dict.items():
            flattened_param = param.view(-1).tolist()
            for value in flattened_param:
                writer.writerow([layer_name, 'weight' if 'weight' in layer_name else 'bias', value])
                
    tst.to_csv(pred_file_path, index=False, header=True)
    
    print(f'finished with seed {i}')


results_file = "results_by_seed"
results_path = os.path.join(os.getcwd(), results_file)

with open(results_path, 'w') as csvfile:
    writer = csv.writer(csvfile)
    
    for index, result in enumerate(seed_results):
        writer.writerow([f"Results for seeed {index + 1}: {result}"])


Downloading...
100%|██████████| 2.57M/2.57M [00:00<00:00, 11.6MiB/s]
Loading...
Downloading...
100%|██████████| 185k/185k [00:00<00:00, 4.58MiB/s]
Loading...
Downloading...
100%|██████████| 202M/202M [00:08<00:00, 22.6MiB/s] 
Downloading...
100%|██████████| 20.5M/20.5M [00:01<00:00, 20.1MiB/s]
Downloading...


downloading pinancle zip data...


100%|██████████| 5.20M/5.20M [00:00<00:00, 24.7MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0003767_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0003767_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0003767_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0000685_torch_mlp_test_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_train_preds_sperm.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_nk cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_nk cell.csv
got file TS_EFO_0003767_torch_mlp_train_preds_sperm.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_test_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_val_preds_nk cell.csv
got file TS_EFO_0000685_torch_mlp_a

Downloading...


...

success!
iterating over csv files...
got file TS_EFO_0000685_torch_mlp_all_preds_esm.csv
got file TS_EFO_0003767_torch_mlp_all_preds_esm.csv
got file TS_EFO_0000685_torch_mlp_test_preds_esm.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_test_preds_esm.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0003767_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_sperm.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_test_preds_sperm.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0000685_torch_mlp_all_preds_nk cell.csv
got file TS_EFO_0003767_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0000685_torch_mlp_val_preds_global.csv
got 

Downloading...


36229
36229
downloading pinancle zip data...


100%|██████████| 6.53M/6.53M [00:00<00:00, 23.8MiB/s]
Extracting zip file...
Done!


success!
iterating over csv files...
got file TS_EFO_0000685_torch_mlp_all_preds_esm.csv
got file TS_EFO_0003767_torch_mlp_all_preds_esm.csv
got file TS_EFO_0000685_torch_mlp_test_preds_esm.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_test_preds_esm.csv
reading into pandas...
got file TS_EFO_0003767_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_all_preds_sperm.csv
got file TS_EFO_0003767_torch_mlp_val_preds_sperm.csv
got file TS_EFO_0000685_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_all_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_test_preds_sperm.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_test_preds_sperm.csv
reading into pandas...
got file TS_EFO_0000685_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0003767_torch_mlp_val_preds_b cell.csv
got file TS_EFO_0000685_torch_mlp_val_preds_global.csv
got file TS_EFO_0003767_torch_mlp_val_preds_global.csv
got f